# Copying Adam Taylor's PCam5c driver to python top layer

In [1]:
from kv260 import BaseOverlay
from pynq.lib.video import *
from PIL import Image as PIL_Image

from pynq.lib.iic import AxiIIC

import numpy as np
from time import sleep

base = BaseOverlay("base.bit", ignore_version=True)



In [2]:
mipi = base.mipi
iic = base.axi_iic
vdma = base.mipi.axi_vdma

Defining key addresses

In [3]:
#define DEMO_MAX_FRAME (720*1280)
#define DEMO_STRIDE (1280*3)
#define DISPLAY_NUM_FRAMES 1
#define cam_gpio XPAR_XGPIOPS_0_DEVICE_ID
#define IIC_cam 			XPAR_XIICPS_0_DEVICE_ID

cam_id = 0x78
iic_cam_addr = 0x3c
sw_iic_addr = 0x74

rx_data = bytes(10)
tx_data = [0,0,0,0,0,0]

Setting the I2C switch

In [4]:
tx_data[0] = 0x04

iic.send(sw_iic_addr,tx_data,1)               # send(address,data,length of data, "option" - not necessary)
status = iic.receive(sw_iic_addr, rx_data, 1)

'Add logic for checking successful write '
'''
if status != 0x01:
  print("Error in ReadChannel... reading,", Status)
'''


'\nif status != 0x01:\n  print("Error in ReadChannel... reading,", Status)\n'

Function to detect the camera - reading the ID

In [5]:
def detect_camera():
    
    tx_data = [0,0,0,0,0]
    tx_data[0] = 0x31;  tx_data[1] = 0x00;

    iic.send(iic_cam_addr,tx_data,2)               # send(address,data,length of data, "option" - not necessary)
    print('send complete')
    status = iic.receive(iic_cam_addr, rx_data, 1)

    if hex(rx_data[0]) != '0x78':
        print("camera not detected")
        print(rx_data)
        
    else:
        print("camera detected")

In [6]:
detect_camera()

send complete
camera detected


Includinmg a section that writes to the CAM_PWUP (cam_gpio) pin as outlined in step one of power up:

note: adam taylor doesn't need this

In [7]:
#note remember the wait for 50ms

# Execute a power-cycle by applying a low pulse of 100ms on CAM_PWUP, then driving it high - writing to cam_gpio 
#base.mipi.gpio_ip_reset[0].write(0) 
#sleep(1)
#base.mipi.gpio_ip_reset[0].write(1) 

Register check for sanity as outlined in step 3 of guide

note: Adam Taylor also doesn't do this

In [8]:
tx_data[0] = 0x30;  tx_data[1] = 0x0A;

iic.send(iic_cam_addr,tx_data,2)               # send(address,data,length of data, "option" - not necessary)
status = iic.receive(iic_cam_addr, rx_data, 1)

if hex(rx_data[0]) != '0x56':
  print("Read fail at register 300A ")
else:
    print("register 300A read correct")

tx_data[0] = 0x30;  tx_data[1] = 0x0B;

iic.send(iic_cam_addr,tx_data,2)               # send(address,data,length of data, "option" - not necessary)
status = iic.receive(iic_cam_addr, rx_data, 1)

if hex(rx_data[0]) != '0x40':
  print("Read fail at register 300A ")
else:
  print("register 300A read correct")

register 300A read correct
register 300A read correct


Step 4 on guide - choosing input clock by writing 0x11 to register address 0x3103.

In [9]:
tx_data[0] = 0x31;  tx_data[1] = 0x03;
tx_data[2] = 0x11

iic.send(iic_cam_addr,tx_data,3)               # send(address,data,length of data, "option" - not necessary)
status = iic.receive(iic_cam_addr, rx_data, 1)

print(hex(rx_data[0]))

0x1


Step 5 Execute software reset by writing 0x82 to register address 0x3008.

In [10]:
tx_data[0] = 0x30;  tx_data[1] = 0x08;
tx_data[2] = 0x82

iic.send(iic_cam_addr,tx_data,3)               # send(address,data,length of data, "option" - not necessary)
status = iic.receive(iic_cam_addr, rx_data, 1)
#print(hex(rx_data[0]))

In [11]:
sleep(1)   # Digilent guide says sleep for 10ms - adam taylor does 1s and his works 

Reaching out to the *cfg_init* structure for the following steps of the guide:


In [12]:
#array and function for extracting and writing the addresses stored here are in the pcam_cfg.py file

%run pcam_cfg.ipynb

In [ ]:
#Sending commands to the addresses as part of the cfg_init library - bulletpoints 6-8 of digi guide
setting_func(cfg_init)

#setting the desired frame rate configurations 
setting_func(cfg_720p_60fps)

print('configuration complete')

0 / 63 0x30 0x8 0x42
recieved =  0x1 0x0 0x0 

1 / 63 0x31 0x3 0x3
recieved =  0x1 0x0 0x0 

2 / 63 0x30 0x17 0x0
recieved =  0x0 0x0 0x0 

3 / 63 0x30 0x18 0x0
recieved =  0xf0 0x0 0x0 

4 / 63 0x30 0x34 0x18
recieved =  0x11 0x0 0x0 

5 / 63 0x30 0x35 0x11
recieved =  0x69 0x0 0x0 

6 / 63 0x30 0x36 0x38
recieved =  0x3 0x0 0x0 

7 / 63 0x30 0x37 0x11
recieved =  0x0 0x0 0x0 

8 / 63 0x31 0x8 0x1
recieved =  0x0 0x0 0x0 

9 / 63 0x30 0x3d 0x10
recieved =  0x0 0x0 0x0 

10 / 63 0x30 0x3b 0x19
recieved =  0x11 0x0 0x0 

11 / 63 0x36 0x30 0x2e
recieved =  0x0 0x0 0x0 

12 / 63 0x36 0x31 0xe
recieved =  0x42 0x0 0x0 

13 / 63 0x36 0x32 0xe2
recieved =  0x23 0x0 0x0 

14 / 63 0x36 0x33 0x23
recieved =  0x14 0x0 0x0 

15 / 63 0x36 0x21 0xe0
recieved =  0x0 0x0 0x0 

16 / 63 0x37 0x4 0xa0
recieved =  0x2a 0x0 0x0 

17 / 63 0x37 0x3 0x5a
recieved =  0xa0 0x0 0x0 

18 / 63 0x37 0x15 0x78
recieved =  0x23 0x0 0x0 

19 / 63 0x37 0x17 0x1
recieved =  0x0 0x0 0x0 

20 / 63 0x37 0xb 0x60
recieved 

Set up Video Timing controller 

In [ ]:
videomode = VideoMode(1280,720,24)
mipi.configure(videomode)

Here Adam taylor configures the VDMA block - does this have to be done in my case? Beyond what I am doing below 

In [ ]:
mipi.start()

In [89]:
rx_data = bytes(10)
tx_data[0] = 0x30;  tx_data[1] = 0x08; tx_data[2] = 0x02;


#iic.send(iic_cam_addr,tx_data,3)               # send(address,data,length of data, "option" - not necessary)
status = iic.receive(iic_cam_addr, rx_data, 1)

print(rx_data)

b'\x00\x00\x00\x00\x00\x00\x00\x00\x00\x00'


Repeating functions for camera detection and resets

In [ ]:
detect_camera()

#choose system input clock from pad
tx_data[0] = 0x31;  tx_data[1] = 0x03;
tx_data[2] = 0x11

iic.send(iic_cam_addr,tx_data,3)               # send(address,data,length of data, "option" - not necessary)
status = iic.receive(iic_cam_addr, rx_data, 1)

'''#EXECUTE SOFTWARE RESET
tx_data[0] = 0x30;  tx_data[1] = 0x08;
tx_data[2] = 0x82

iic.send(iic_cam_addr,tx_data,3)               # send(address,data,length of data, "option" - not necessary)
status = iic.receive(iic_cam_addr, rx_data, 1)
'''

In [ ]:
sleep(1)

Adam Taylor then resends the commands to read through all three configuration files

In [ ]:
#Sending commands to the addresses as part of the cfg_init library - bulletpoints 6-8 of digi guide
setting_func(cfg_init)

setting_func(cfg_simple_awb)

#setting the desired frame rate configurations 
setting_func(cfg_720p_60fps)

print('configuration complete')

Adam Taylor then starts his vdma block by writing to it 

In [ ]:
frame = mipi.readframe()

In [ ]:
frame = mipi.axi_vdma.S2MMChannel()